In [1]:
%cd ..

/home/nikita/edu/competitions/admet


In [2]:
import numpy as np
import pandas as pd

import datamol as dm

from molfeat.calc import RDKitDescriptors2D, FPCalculator, MordredDescriptors
from molfeat.trans import MoleculeTransformer
from molfeat.trans.concat import FeatConcat
from molfeat.trans.fp import FPVecTransformer

from catboost import CatBoostClassifier

In [9]:
train_data = dm.read_csv("data/shuffled_final_extended_train_data.csv", smiles_column="Drug")

[10:10:43] SMILES Parse Error: extra open parentheses for input: 'COP(=S)(OCC)Oc1ccc(N)c(CCС)c1'
[10:10:43] SMILES Parse Error: extra open parentheses for input: 'COC(=O)C1=C(CCС)NC(CCС)=C(C(=O)OC)C1c1ccccc1[N+](=O)[O-]'
[10:10:43] SMILES Parse Error: extra open parentheses for input: 'Cc1ccc(CCС)o1'
[10:10:43] SMILES Parse Error: extra open parentheses for input: 'C=CCOc1ccccc1OCC(O)CNC(CCС)C'
[10:10:43] SMILES Parse Error: extra open parentheses for input: 'CC1=C(NC2=CC=CC=C12)CN(CCС)C3=NC(=NC(=C3)C4CC(C4)O)N'
[10:10:43] SMILES Parse Error: extra open parentheses for input: 'CN(CCС)CCCC1c2ccccc2Nc2ccc(Cl)cc21'
[10:10:43] SMILES Parse Error: extra open parentheses for input: 'CC1COc2c(N3CCN(CCС)CC3)c(F)c(C(=O)O)c3c(=O)ccn1c23'
[10:10:43] SMILES Parse Error: extra open parentheses for input: 'CN(CCС)c1nc(N(CCС)C)nc(N(CCС)C)n1'
[10:10:43] SMILES Parse Error: extra open parentheses for input: 'CCN(CCС)CCNC(=O)c1cc(Cl)cc(Cl)c1OC'
[10:10:43] SMILES Parse Error: extra open parentheses for i

In [10]:
train_data.dropna(inplace=True)

In [5]:
rdkit = FPVecTransformer("desc2D", n_jobs=8, dtype=np.float32, replace_nan=True)
maccs = FPVecTransformer("maccs", dtype=np.float32)
ecfp4 = FPVecTransformer("ecfp:4", dtype=np.float32)

# Wrap the calculator in a transformer instance
featurizer = FeatConcat([maccs, ecfp4, rdkit], dtype=np.float32)

with dm.without_rdkit_log():
    feats = featurizer(train_data["mol"])

/home/nikita/edu/competitions/admet/.conda/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
[10:08:46] DEPRECATION WARNING: please use MorganGenerator
[10:08:46] DEPRECATION WARNING: please use MorganGenerator
[10:08:46] DEPRECATION WARNING: please use MorganGenerator
[10:08:46] DEPRECATION WARNING: please use MorganGenerator
[10:08:46] DEPRECATION WARNING: please use MorganGenerator
[10:08:46] DEPRECATION WARNING: please use MorganGenerator
[10:08:46] DEPRECATION WARNING: please use MorganGenerator
[10:08:46] DEPRECATION WARNING: please use MorganGenerator
[10:08:46] DEPRECATION WARNING: please use MorganGenerator
[10:08:46] DEPRECATION WARNING: please use MorganGenerator
[10:08:46] DEPRECATION WARNING: please use MorganGenerator
[10:08:46] DEPRECATION WARNING: please use MorganGenerator
[10:08:46] DEPR

In [12]:
train_data.reset_index(inplace=True, drop=True)

In [13]:
feature_cols = [f"{i}" for i in range(feats.shape[1])]
feats = pd.DataFrame(feats, columns=feature_cols)
train_data = pd.concat([train_data, feats], axis=1)

In [15]:
properties = train_data.property.unique()
train_dfs = []
for prop in properties:
    train_dfs.append(train_data[train_data.property == prop])

In [16]:
models = []
for train_df in train_dfs:
    X = train_df[feature_cols]
    y = train_df["Y"]
    model = CatBoostClassifier(n_estimators=1000, eval_metric="AUC", eval_fraction=0.1)
    model.fit(X, y)
    models.append(model)

Learning rate set to 0.058478
0:	test: 0.7879777	best: 0.7879777 (0)	total: 70.9ms	remaining: 1m 10s
1:	test: 0.7931564	best: 0.7931564 (1)	total: 87.5ms	remaining: 43.7s
2:	test: 0.8133903	best: 0.8133903 (2)	total: 106ms	remaining: 35.1s
3:	test: 0.8229893	best: 0.8229893 (3)	total: 120ms	remaining: 29.9s
4:	test: 0.8275083	best: 0.8275083 (4)	total: 140ms	remaining: 27.9s
5:	test: 0.8293116	best: 0.8293116 (5)	total: 157ms	remaining: 26.1s
6:	test: 0.8340413	best: 0.8340413 (6)	total: 176ms	remaining: 24.9s
7:	test: 0.8368432	best: 0.8368432 (7)	total: 195ms	remaining: 24.2s
8:	test: 0.8384606	best: 0.8384606 (8)	total: 220ms	remaining: 24.2s
9:	test: 0.8412363	best: 0.8412363 (9)	total: 238ms	remaining: 23.6s
10:	test: 0.8405801	best: 0.8412363 (9)	total: 256ms	remaining: 23s
11:	test: 0.8405438	best: 0.8412363 (9)	total: 276ms	remaining: 22.8s
12:	test: 0.8422168	best: 0.8422168 (12)	total: 295ms	remaining: 22.4s
13:	test: 0.8454425	best: 0.8454425 (13)	total: 311ms	remaining: 21.

In [21]:
test_data = dm.read_csv("data/test_data.csv", smiles_column="Drug")

[10:13:23] WARNING: not removing hydrogen atom without neighbors
[10:13:23] WARNING: not removing hydrogen atom without neighbors
[10:13:23] WARNING: not removing hydrogen atom without neighbors
[10:13:23] WARNING: not removing hydrogen atom without neighbors
[10:13:23] WARNING: not removing hydrogen atom without neighbors
[10:13:23] WARNING: not removing hydrogen atom without neighbors
[10:13:23] WARNING: not removing hydrogen atom without neighbors
[10:13:23] WARNING: not removing hydrogen atom without neighbors
[10:13:23] WARNING: not removing hydrogen atom without neighbors
[10:13:23] WARNING: not removing hydrogen atom without neighbors
[10:13:23] WARNING: not removing hydrogen atom without neighbors


In [23]:
with dm.without_rdkit_log():
    test_feats = featurizer(test_data["mol"])

[10:13:31] DEPRECATION WARNING: please use MorganGenerator
[10:13:31] DEPRECATION WARNING: please use MorganGenerator
[10:13:31] DEPRECATION WARNING: please use MorganGenerator
[10:13:31] DEPRECATION WARNING: please use MorganGenerator
[10:13:31] DEPRECATION WARNING: please use MorganGenerator
[10:13:31] [10:13:31] DEPRECATION WARNING: [10:13:31] please use MorganGeneratorDEPRECATION WARNING: please use MorganGenerator

DEPRECATION WARNING: [10:13:31] DEPRECATION WARNING: please use MorganGenerator
please use MorganGenerator
[10:13:31] [10:13:31] DEPRECATION WARNING: please use MorganGenerator
[10:13:31] [10:13:31] DEPRECATION WARNING: please use MorganGenerator
DEPRECATION WARNING: please use MorganGenerator
[10:13:31] DEPRECATION WARNING: please use MorganGenerator
[10:13:31] DEPRECATION WARNING: please use MorganGenerator
DEPRECATION WARNING: please use MorganGenerator
[10:13:31] DEPRECATION WARNING: please use MorganGenerator[10:13:31] DEPRECATION WARNING: please use MorganGenerato

In [24]:
test_feats = pd.DataFrame(test_feats, columns=feature_cols)
test_data = pd.concat([test_data, test_feats], axis=1)

In [26]:
all_preds = []
for i, prop in enumerate(properties):
    x = test_data[test_data.property == prop][feature_cols]
    preds = models[i].predict_proba(x)[:, 1]
    all_preds.append(preds)

In [32]:
sample = pd.read_csv("data/sample.csv")
sample["Y"] = np.concatenate(all_preds)
sample.to_csv("submissions/catboost_dirty.csv", index=False)